In [216]:
import nltk; nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\eric_\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [217]:
import re
import numpy as np 
import pandas as pd

from pprint import pprint

In [218]:
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

In [219]:
import spacy
nlp = spacy.load("en_core_web_sm")

In [220]:
# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  
import matplotlib.pyplot as plt
%matplotlib inline

# Enable logging for gensim
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)

import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

In [221]:
#nltk stop words
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
stop_words.extend(['from','subject','re','edu','use'])

In [222]:
import os
os.environ["GOOGLE_APPLICATION_CREDENTIALS"]="C:\\Users\\eric_\\Downloads\\My Project-499-f28c2476b9b8.json"

In [223]:
from google.cloud import bigquery
client = bigquery.Client()

In [224]:
sql = '''
        SELECT title
        FROM `bigquery-public-data.stackoverflow.tags` FULL OUTER Join `bigquery-public-data.stackoverflow.posts_questions`
        ON tag_name = tags
        where tags like'%flutter%' and score > 1
        order by score desc
'''
query_job = client.query(
    sql,
    location="US",
)
flutter = []
for row in query_job:
    flutter += row
print(flutter)


['How to remove debug banner in flutter on android emulator?', "Couldn't locate lint-gradle-api-26.1.2.jar for Flutter project", 'flutter run: No connected devices', 'How to create Toast in Flutter?', 'TextField inside of Row causes layout exception: Unable to calculate size', 'How to change the application launcher icon on Flutter?', 'How do I use hexadecimal color strings in Flutter?', 'Sizing elements to percentage of screen width/height', 'Adding a splash screen to Flutter apps', 'Equivalent of RelativeLayout in Flutter', 'Scaffold.of() called with a context that does not contain a Scaffold', 'How can I save to local storage using Flutter?', 'Flutter: How to correctly use an Inherited Widget?', 'How do I supply an initial value to a text field?', 'How do I add a border to a widget, in Flutter?', 'How do I do the "frosted glass" effect in Flutter?', 'Create a rounded button / button with border-radius in Flutter', 'What is the difference between functions and classes to create widge

In [202]:
#tokenize words 
def tokenize_words(txt):
    for sentence in txt:
        yield(gensim.utils.simple_preprocess(str(txt), deacc=True)) #deacc removes punctuations

data_words = list(tokenize_words(flutter))
#print(data_words)

In [203]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(data_words, min_count=5, threshold=50) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[data_words], threshold=50)

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

# See trigram example
#print(trigram_mod[bigram_mod[data_words[0]]])

In [204]:
# Define functions for stopwords, bigrams, trigrams and lemmatization
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]

def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [205]:
# Remove Stop Words
data_words_nostops = remove_stopwords(data_words)

# Form Bigrams
data_words_bigrams = make_bigrams(data_words_nostops)

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
data_lemmatized = lemmatization(data_words_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

print(data_lemmatized)

[['emulator', 'run', 'connect', 'device', 'create', 'toast', 'flutter', 'change', 'application', 'row', 'cause', 'layout', 'exception', 'unable', 'calculate', 'size', 'hexadecimal', 'color', 'string', 'sizing', 'element', 'percentage', 'screen', 'width', 'height', 'add', 'splash', 'screen', 'flutter', 'call', 'context', 'contain', 'scaffold', 'supply', 'initial', 'value', 'text', 'correctly', 'inherit', 'widget', 'save', 'local', 'storage', 'use', 'flutter', 'frosted', 'glass', 'effect', 'add', 'border', 'widget', 'flutter', 'create', 'round', 'button', 'button', 'border', 'difference', 'function', 'class', 'create', 'widget', 'render', 'equivalent', 'flutter', 'pass', 'datum', 'stateful', 'configure', 'relation', 'stateful', 'stateless', 'widget', 'flutter', 'detect', 'host', 'add', 'flutter', 'key', 'stateless', 'class', 'flutter', 'make', 'textfield', 'underline', 'deal', 'unwanted', 'widget', 'build', 'create', 'overflow', 'ellipsis', 'text', 'round', 'corner', 'image', 'flutter', 

In [206]:
# Create Dictionary
id2word = corpora.Dictionary(data_lemmatized)

# Create Corpus
texts = data_lemmatized

# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]

# View
print(corpus[:1])

[[(0, 1), (1, 1), (2, 3), (3, 2), (4, 2), (5, 17), (6, 1), (7, 2), (8, 2), (9, 1), (10, 16), (11, 3), (12, 1), (13, 1), (14, 1), (15, 8), (16, 1), (17, 1), (18, 6), (19, 1), (20, 1), (21, 2), (22, 1), (23, 1), (24, 1), (25, 2), (26, 1), (27, 3), (28, 8), (29, 2), (30, 6), (31, 3), (32, 1), (33, 1), (34, 2), (35, 1), (36, 1), (37, 1), (38, 5), (39, 4), (40, 1), (41, 2), (42, 1), (43, 1), (44, 1), (45, 1), (46, 8), (47, 1), (48, 7), (49, 1), (50, 8), (51, 1), (52, 1), (53, 4), (54, 1), (55, 3), (56, 1), (57, 29), (58, 1), (59, 1), (60, 4), (61, 4), (62, 1), (63, 2), (64, 1), (65, 1), (66, 6), (67, 1), (68, 2), (69, 3), (70, 1), (71, 4), (72, 2), (73, 1), (74, 6), (75, 1), (76, 19), (77, 6), (78, 1), (79, 1), (80, 3), (81, 1), (82, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 1), (88, 2), (89, 1), (90, 2), (91, 1), (92, 1), (93, 2), (94, 1), (95, 3), (96, 1), (97, 1), (98, 1), (99, 3), (100, 2), (101, 1), (102, 1), (103, 16), (104, 1), (105, 3), (106, 4), (107, 1), (108, 1), (109, 11), (1

In [207]:
# Human readable format of corpus (term-frequency)
[[(id2word[id], freq) for id, freq in cp] for cp in corpus[:1]]

[[('able', 1),
  ('accept', 1),
  ('access', 3),
  ('accord', 2),
  ('action', 2),
  ('add', 17),
  ('alert', 1),
  ('align', 2),
  ('already', 2),
  ('anchor', 1),
  ('android', 16),
  ('animation', 3),
  ('anywhere', 1),
  ('api', 1),
  ('apiexception', 1),
  ('app', 8),
  ('appear', 1),
  ('apple', 1),
  ('application', 6),
  ('arabic', 1),
  ('argument', 1),
  ('asset', 2),
  ('augment', 1),
  ('authentication', 1),
  ('automatically', 1),
  ('available', 2),
  ('avatar', 1),
  ('back', 3),
  ('background', 8),
  ('bad', 2),
  ('bar', 6),
  ('base', 3),
  ('big', 1),
  ('bit', 1),
  ('block', 2),
  ('blur', 1),
  ('body', 1),
  ('bold', 1),
  ('border', 5),
  ('bottom', 4),
  ('bottomsheet', 1),
  ('box', 2),
  ('boxdecoration', 1),
  ('bracket', 1),
  ('bring', 1),
  ('browser', 1),
  ('build', 8),
  ('builder', 1),
  ('button', 7),
  ('calculate', 1),
  ('call', 8),
  ('callback', 1),
  ('capture', 1),
  ('card', 4),
  ('catch', 1),
  ('cause', 3),
  ('center', 1),
  ('change', 2

In [212]:
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics= 3, 
                                           random_state=20,
                                           update_every=1,
                                           chunksize=500,
                                           passes=15,
                                           alpha=15,
                                           per_word_topics=True)

In [213]:
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(0,
  '0.082*"flutter" + 0.036*"widget" + 0.018*"use" + 0.017*"change" + '
  '0.014*"text" + 0.013*"color" + 0.013*"android" + 0.013*"image" + '
  '0.012*"screen" + 0.011*"create"'),
 (1,
  '0.067*"flutter" + 0.036*"widget" + 0.022*"change" + 0.018*"text" + '
  '0.017*"use" + 0.015*"screen" + 0.014*"image" + 0.013*"color" + 0.013*"add" '
  '+ 0.010*"create"'),
 (2,
  '0.060*"flutter" + 0.027*"widget" + 0.024*"change" + 0.018*"use" + '
  '0.016*"color" + 0.016*"text" + 0.014*"add" + 0.013*"create" + 0.013*"image" '
  '+ 0.013*"android"')]


In [214]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. lower the better.

# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_lemmatized, dictionary=id2word, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Perplexity:  -5.59574979724237

Coherence Score:  0.2305194461436866


In [215]:
# Visualize the topics
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
vis

C:\Users\eric_\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.003918 -0.000210       1        1  33.378036
0      0.002176 -0.002742       2        1  33.325069
1      0.001742  0.002952       3        1  33.296898, topic_info=    Category          Freq      Term         Total  loglift  logprob
177  Default  43656.000000   flutter  43656.000000  30.0000  30.0000
505  Default  20678.000000    widget  20678.000000  29.0000  29.0000
57   Default  13334.000000    change  13334.000000  28.0000  28.0000
502  Default   3216.000000       way   3216.000000  27.0000  27.0000
309  Default   2760.000000      open   2760.000000  26.0000  26.0000
..       ...           ...       ...           ...      ...      ...
10    Topic3   1982.273315   android   7356.299805  -0.2116  -4.6584
474   Topic3   1221.371948      type   3677.791992  -0.0026  -5.1427
442   Topic3   1291.415283    studio   4138.540039  -0.0649  -5.0869
195   Topic3   1487.440430       get   5516.790527  -0.2110  -4.9456
427   Topic3   1090.609619  stateful   3678.612549  -0.1161  -5.2559

[224 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
2         1  0.249411  access
2         2  0.326989  access
2         3  0.423418  access
3         1  0.387807  accord
3         2  0.205310  accord
...     ...       ...     ...
509       2  0.367994    work
509       3  0.337902    work
511       1  0.295338  yellow
511       2  0.284480  yellow
511       3  0.421291  yellow

[417 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 1, 2])